The goal of this project is to learn how to harvest data from OpenStreetMap and vizualise the data. As usual, before start writting the code let's import all libraries needed.

In [1]:
import overpy
import pandas as pd
from shapely.geometry import Point, LineString
from geopandas import GeoDataFrame
import folium
from geopy.geocoders import Nominatim

Next step is creating a function to collect data from OSM using overpy library. 

In [2]:
def collect_osm_data(city_name,key,value):
    

    # Geocoding request via Nominatim
    geolocator = Nominatim(user_agent="city_compare")
    geo_results = geolocator.geocode(city_name, exactly_one=False, limit=3)
    
    # find the first element in geo_results where osm_type = "relation"
    for r in geo_results:
        if r.raw.get("osm_type") == "relation":
            city = r
            break


    # Calculating area id
    area_id = int(city.raw.get("osm_id")) + 3600000000
    
    api = overpy.Overpass()
    
    result = api.query("""
    area(%s)->.searchArea;
    (
      node[%s=%s](area.searchArea);
      way[%s=%s](area.searchArea);
      relation[%s=%s](area.searchArea);
    );
    out body;
    >;
    out skel qt;
        """ % (area_id,key,value,key,value,key,value))
    return result

# Point of Interest (School)

The first task is to visualize point of interest data. For the first step, I use the function to retreive data of all schools in Salatiga. 

In [3]:
result = collect_osm_data("salatiga","amenity","school")

Next is to convert the result into tabular format. Since I want all of the data is in single point format, therefore I need to convert data in way element into single point. The simple way that I can think of is by getting the longitude and latitude of the first node in each way element.

In [4]:
cols = ['id','name','lat', 'lon']
lst = []
for x in result.nodes:
    lst.append([x.id,x.tags.get("name"),float(x.lat), float(x.lon)])
for x in result.ways:
    lst.append([x.id,x.tags.get("name"),float(x.nodes[0].lat),float(x.nodes[0].lon)])

df_poi = pd.DataFrame(lst, columns=cols)
    
df_poi

id                       name       lat         lon
0    2141230413          Ex SMA Theresiana -7.314217  110.496735
1    3256274562            SMPN 5 Salatiga -7.338634  110.485624
2    3362897085      SMP Negeri 4 Salatiga -7.322150  110.503297
3    4777230597      MI Ma'arif Mangunsari -7.329276  110.491124
4    4950042048        SMP Stella Matutina -7.320914  110.498467
..          ...                        ...       ...         ...
363   722090384      SMP Negeri 9 Salatiga -7.323936  110.506157
364   722227939  SMP Muhammadiyah Salatiga -7.322360  110.498225
365   297305121                       None -7.326821  110.498698
366   297144489                       None -7.328295  110.496430
367   297144490                       None -7.328651  110.496076

[368 rows x 4 columns]

Next is cleaning the data from records without name

In [5]:
df_poi = df_poi[df_poi['name'].isnull() == False]

I want to group the school based on education level, to do this I check the name of each data points and categorize it based on whether it contains specific character

In [6]:
df_poi.loc[df_poi['name'].str.contains("SD"),'education_level'] = 'Primary School'
df_poi.loc[df_poi['name'].str.contains("SMP"),'education_level'] = 'Junior High School'
df_poi.loc[df_poi['name'].str.contains("SMA"),'education_level'] = 'Senior High School'
df_poi.loc[~df_poi['education_level'].isin(['Primary School','Junior High School','Senior High School']),'education_level'] = 'Unidentified'

/opt/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:376: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[key] = _infer_fill_value(value)
/opt/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:494: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s


I admit it that the way I categorize the school is not really accurate since there are school using english name or mix between primary and junior high school, but this is the best way I can think right now. Now let's display the result using bar chart

In [7]:
df_barchart = df_poi.groupby('education_level').count().reset_index()

from plotly import graph_objects as go


fig = go.Figure(
    data = [
        go.Bar(
            name="Original",
            x=df_barchart["education_level"],
            y=df_barchart["id"],
            offsetgroup=0,
        ),
    ],
    layout=go.Layout(
        title="School Types in Salatiga - Based on Education Level",
        yaxis_title="Number of Schools"
    )
)
fig.show()

The result is not suprise as it is obvious that there are more primary school than high school. Now let's show a map of all schools in Salatiga using Folium.

In [8]:
m = folium.Map([-7.33194, 110.49278], zoom_start=10, tiles="CartoDb dark_matter")
locs = zip(df_poi['lat'], df_poi['lon'])
#folium.GeoJson(buildings, style_function=lambda x: style_buildings).add_to(m)
for location in locs:
    folium.CircleMarker(location=location, 
        color = "#F4F6F7",   radius=2).add_to(m)
#m.save("school_map.html")
m

# Street (Primary)

The second task is to visualize street data. For the first step, I use the function to retreive data of all primary highway in Salatiga. 

In [9]:
result = collect_osm_data("salatiga","highway","primary")

Since this is a street data, I only use way element which basically a collection of node elements that have relation.

In [10]:
cols = ['id','name','lat','lon']
lst = []
for x in result.ways:
    for y in x.nodes:
        lst.append([x.id,x.tags.get("name"),float(y.lat),float(y.lon)])
df_highway = pd.DataFrame(lst, columns=cols)

In [11]:
df_highway.head()

id                  name       lat         lon
0  23783033  Jalan Soekarno-Hatta -7.354928  110.512790
1  23783033  Jalan Soekarno-Hatta -7.355119  110.512819
2  23783033  Jalan Soekarno-Hatta -7.356652  110.513038
3  23783033  Jalan Soekarno-Hatta -7.358135  110.513228
4  23783033  Jalan Soekarno-Hatta -7.358708  110.513301

As you can see the data is represented in point based format (node). So before it can be visualised, I need to group these points based on id column and then arrange the points sequentially in time to create a LineString object for each id.

In [12]:
# Zip the coordinates into a point object and convert to a GeoDataFrame
geometry = [Point(xy) for xy in zip(df_highway.lon, df_highway.lat)]
gdf_highway = GeoDataFrame(df_highway, geometry=geometry)
# Aggregate these points with the GroupBy
gdf_highway = gdf_highway.groupby(['id'])['geometry'].apply(lambda x: LineString(x.tolist()))
gdf_highway = GeoDataFrame(gdf_highway, geometry='geometry')

In [13]:
gdf_highway.head()

geometry
id                                                          
23783033   LINESTRING (110.51279 -7.35493, 110.51282 -7.3...
24267849   LINESTRING (110.49751 -7.31929, 110.49775 -7.3...
43361966   LINESTRING (110.50477 -7.32465, 110.50472 -7.3...
104244695  LINESTRING (110.51368 -7.36184, 110.51393 -7.3...
167909069  LINESTRING (110.50466 -7.32493, 110.50425 -7.3...

Now the data is in the correct format. let's show a map of primary highway in Salatiga using Folium.

In [14]:
gdf_highway.crs = {'init' :'epsg:4326'}
style = {'color': '#F7DC6F', 'weight':'1'}
m = folium.Map([-7.33194, 110.49278],
zoom_start=15,
tiles="CartoDb dark_matter")
folium.GeoJson(gdf_highway, style_function=lambda x: style).add_to(m)
m

/opt/anaconda3/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning:

'+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6



# Street (Residential)

Since a street in OSM consists of more than one node, below I build a script to display the street and their nodes in one map. I also use colour to distinguish a street that contain one line (red colour) and multiple lines (white colour). For the location I choose Mildura, a small city in Victoria, Australia.

In [15]:
result = collect_osm_data("mildura","highway","residential")

In [16]:
cols = ['id','name','lat','lon']
lst = []
for x in result.ways:
    for y in x.nodes:
        lst.append([x.id,x.tags.get("name"),float(y.lat),float(y.lon)])
df_highway = pd.DataFrame(lst, columns=cols)

In [17]:
df_highway['count'] = df_highway.groupby('id')['id'].transform('count')

In [18]:
df_highway

id               name        lat         lon  count
0      22635949      Orange Avenue -34.191293  142.159393      2
1      22635949      Orange Avenue -34.191218  142.159482      2
2      22635950      Madden Avenue -34.190444  142.158376      4
3      22635950      Madden Avenue -34.190355  142.158478      4
4      22635950      Madden Avenue -34.190302  142.158532      4
...         ...                ...        ...         ...    ...
6677  753922222          Cleek Way -34.178836  142.140255      6
6678  753922222          Cleek Way -34.178820  142.140201      6
6679  753922222          Cleek Way -34.178826  142.140148      6
6680  762969055  Thirteenth Street -34.192338  142.153651      2
6681  762969055  Thirteenth Street -34.192524  142.153870      2

[6682 rows x 5 columns]

In [19]:
# Zip the coordinates into a point object and convert to a GeoDataFrame
geometry = [Point(xy) for xy in zip(df_highway.lon, df_highway.lat)]
gdf_highway = GeoDataFrame(df_highway, geometry=geometry)
# Aggregate these points with the GroupBy
gdf_highway = gdf_highway.groupby(['id','name','count'])['geometry'].apply(lambda x: LineString(x.tolist()))
gdf_highway = GeoDataFrame(gdf_highway, geometry='geometry')
gdf_highway = gdf_highway.reset_index()

In [20]:
gdf_highway.head(100)

id                name  count  \
0   22635949       Orange Avenue      2   
1   22635950       Madden Avenue      4   
2   22636450  Seventeenth Street      5   
3   23224324      Seventh Street      2   
4   23224405     Benetook Avenue      8   
..       ...                 ...    ...   
95  76536203       Eighth Street      3   
96  76536204        Tenth Street      3   
97  76536205        Tenth Street      3   
98  76536208        Tenth Street      8   
99  76536211       Eighth Street      7   

                                             geometry  
0   LINESTRING (142.15939 -34.19129, 142.15948 -34...  
1   LINESTRING (142.15838 -34.19044, 142.15848 -34...  
2   LINESTRING (142.12969 -34.23592, 142.12541 -34...  
3   LINESTRING (142.16437 -34.18357, 142.16420 -34...  
4   LINESTRING (142.18038 -34.19550, 142.18077 -34...  
..                                                ...  
95  LINESTRING (142.15483 -34.17853, 142.15471 -34...  
96  LINESTRING (142.15677 -34.18608, 142.15649 -34...  
97  LINESTRING (142.14452 -34.17580, 142.14441 -34...  
98  LINESTRING (142.15386 -34.18363, 142.15301 -34...  
99  LINESTRING (142.15043 -34.17485, 142.15037 -34...  

[100 rows x 4 columns]

In [21]:
gdf_highway.crs = {'init' :'epsg:4326'}
m = folium.Map([-34.206841, 142.136490],
zoom_start=15,
tiles="CartoDb dark_matter")
folium.GeoJson(gdf_highway, style_function=lambda x: {'color': '#ffffff', 'weight':'1'}).add_to(m)
folium.GeoJson(gdf_highway[gdf_highway['count'] <= 2], style_function=lambda x: {'color': '#e6053a', 'weight':'1'}).add_to(m)
locs = zip(df_highway['lat'], df_highway['lon'])
for location in locs:
    folium.CircleMarker(location=location, 
        color = "#107b21",   radius=0.1).add_to(m)
m

/opt/anaconda3/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning:

'+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6



# Radius Search

Now let's see if I want to find and categorize streets based on their distance to certain point. First, I create a new function for user to find stret based on radius distance.

In [22]:
def radius_osm(key,value,radius,lat,long):
    
    
    api = overpy.Overpass()
    
    result = api.query("""
    (
      node[%s~%s](around:%s,%s,%s);
      way[%s~%s](around:%s,%s,%s);
      relation[%s~%s](around:%s,%s,%s);
    );
    out body;
    >;
    out skel qt;
        """ % (key,value,radius,lat,long,key,value,radius,lat,long,key,value,radius,lat,long))
    return result



Next I create a loop since I need to collect streets in 3 different radius distance (800,1000, & 1200 m)

In [23]:
cols = ['id','name','lat','lon','radius']
lst = []
for value in ["motorway","primary", "primary_link","secondary", "secondary_link","residential"]:
    for rad in [800,1000,1200]:
        result = radius_osm("highway",value,rad, -34.206841, 142.136490)
        for x in result.ways:
            for y in x.nodes:
                lst.append([x.id,x.tags.get("name"),float(y.lat),float(y.lon),rad])
df_highway = pd.DataFrame(lst, columns=cols)

In [24]:
# Zip the coordinates into a point object and convert to a GeoDataFrame
geometry = [Point(xy) for xy in zip(df_highway.lon, df_highway.lat)]
gdf_highway = GeoDataFrame(df_highway, geometry=geometry)
# Aggregate these points with the GroupBy
gdf_highway = gdf_highway.groupby(['id','radius'])['geometry'].apply(lambda x: LineString(x.tolist()))
gdf_highway = GeoDataFrame(gdf_highway, geometry='geometry')

In [25]:
gdf_highway = gdf_highway.reset_index()
gdf_highway = gdf_highway.loc[gdf_highway.groupby('id')['radius'].idxmin()]

In [26]:
gdf_highway

id  radius                                           geometry
0     42643181     800  LINESTRING (142.14174 -34.21067, 142.14204 -34...
3     76340807     800  LINESTRING (142.13231 -34.20994, 142.13258 -34...
6     76340896     800  LINESTRING (142.13574 -34.20746, 142.13573 -34...
9     76699487    1200  LINESTRING (142.13982 -34.19693, 142.14000 -34...
10    76699623     800  LINESTRING (142.14235 -34.20551, 142.14173 -34...
..         ...     ...                                                ...
450  639388326     800  LINESTRING (142.13011 -34.20712, 142.13014 -34...
453  640253480    1000  LINESTRING (142.12545 -34.20509, 142.12604 -34...
455  640330047    1000  LINESTRING (142.14487 -34.20082, 142.14481 -34...
457  644445007     800  LINESTRING (142.12811 -34.20873, 142.12804 -34...
460  698102958    1000  LINESTRING (142.13870 -34.21563, 142.13870 -34...

[221 rows x 3 columns]

In [27]:
gdf_highway.crs = {'init' :'epsg:4326'}
m = folium.Map([-34.206841, 142.136490],
zoom_start=15,
tiles="CartoDb dark_matter")
folium.GeoJson(gdf_highway[gdf_highway['radius'] == 1200], style_function=lambda x: {'color': '#e42a66', 'weight':'1'}).add_to(m)
folium.GeoJson(gdf_highway[gdf_highway['radius'] == 1000], style_function=lambda x: {'color': '#2a3be4', 'weight':'1'}).add_to(m)
folium.GeoJson(gdf_highway[gdf_highway['radius'] == 800], style_function=lambda x: {'color': '#e4d92a', 'weight':'1'}).add_to(m)
folium.CircleMarker(location=(-34.206841, 142.136490), color = "#F4F6F7", radius=4).add_to(m)
folium.Circle([-34.206841, 142.136490], color = '#e4d92a',radius=800).add_to(m)
folium.Circle([-34.206841, 142.136490], color = '#2a3be4',radius=1000).add_to(m)
folium.Circle([-34.206841, 142.136490], color = '#e42a66',radius=1200).add_to(m)
m

/opt/anaconda3/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning:

'+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6

